# Análisis descriptivo COVID-19 | España

Github realiza un renderizado estático de los notebook y no incluye el HTML/JavaScript incrustado que compone un gráfico plotly, para una **correcta visualización**: <a href="https://nbviewer.org/github/pachums/python_projects/blob/main/Covid_19/resumen_covid.ipynb">enlace nbviewer</a> 

Se pueden instalar las librerias o utilizar un **docker** que se ha creado para el experimento, para utilizarlo es necesario descargar **<a href="https://www.docker.com/products/docker-desktop">Docker Desktop</a>** y descargar la imagen del docker con el siguiente comando:
```
docker pull pachums/data-science-ml:v2.3
```
A continuación creamos un container de a partir de la imagen, hemos de definir el directorio donde se alojará el archivo:
```
docker run -p 8888:8888 -v <URL>:/home/jovyan/work pachums/data-science-ml:v2.3
```

In [1]:
import matplotlib.pyplot as plt
import numpy as np
import pandas as pd
import geopandas as gpd
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import math

### Desde el inicio de la pandemia

In [2]:
datos_covid = pd.read_csv("datos/datos_covid_tratados.csv")
datos_covid['fecha'] = pd.to_datetime(datos_covid['fecha'])

 # eliminamos registros previos al inicio de los casos en España
datos_covid = datos_covid[datos_covid['fecha']>=pd.to_datetime('2020-02-21')]

print(f"¡Datos cargados correctamente! Fecha de actualización: {str(datos_covid.iloc[-1][0])[0:10]}")

¡Datos cargados correctamente! Fecha de actualización: 2022-02-10


In [12]:
 # agrupamos por fecha
df = datos_covid.groupby(['fecha'],as_index=False).agg({
    'num_casos': np.sum, 'num_def': np.sum, 'num_hosp': np.sum, 'num_uci': np.sum})

 # creamos las dos visualizaciones
fig = make_subplots(rows=2, cols=1, shared_xaxes=False, 
                    subplot_titles =['Número de casos y hospitalizados','Número de defunciones'])
 # 1 plot
fig.add_trace(go.Bar(x=df['fecha'], y=df['num_casos'], name = "num_casos"), row=1, col=1)

fig.add_trace(go.Scatter(x=df['fecha'], y=df['num_hosp'], name = "num_hosp", line_shape = 'spline', mode='lines', 
                         line = dict(color='black', width=1, dash='solid')), row=1, col=1)
 # 2 plot
fig.add_trace(go.Bar(x=df['fecha'], y=df['num_def'], name = 'num_def'),
    row=2, col=1)

 # anotaciones plot
fig.add_vrect(x0="2020-03-10", x1="2020-05-01", fillcolor="LightSalmon", opacity=0.3, layer="below", line_width=0)
fig.add_vrect(x0="2020-08-04", x1="2020-12-01", fillcolor="LightSalmon", opacity=0.3, layer="below", line_width=0)
fig.add_vrect(x0="2020-12-09", x1="2021-03-12", fillcolor="LightSalmon", opacity=0.3, layer="below", line_width=0)
fig.add_vrect(x0="2021-03-23", x1="2021-05-22", fillcolor="LightSalmon", opacity=0.3, layer="below", line_width=0)
fig.add_vrect(x0="2021-07-05", x1="2021-08-15", fillcolor="LightSalmon", opacity=0.3, layer="below", line_width=0)
fig.add_vrect(x0="2021-11-23", x1="2022-02-10", fillcolor="LightSalmon", opacity=0.3, layer="below", line_width=0)

fig.add_annotation(x="2020-04-07", y=68000, text="1ª ola", showarrow=False, font=dict(family="Old Standard TT, serif", size=14, color="grey"), row=1, col=1)
fig.add_annotation(x="2020-10-01", y=68000, text="2ª ola", showarrow=False, font=dict(family="Old Standard TT, serif", size=14, color="grey"), row=1, col=1)
fig.add_annotation(x="2021-01-27", y=68000, text="3ª ola", showarrow=False, font=dict(family="Old Standard TT, serif", size=14, color="grey"), row=1, col=1)
fig.add_annotation(x="2021-04-22", y=68000, text="4ª ola", showarrow=False, font=dict(family="Old Standard TT, serif", size=14, color="grey"), row=1, col=1)
fig.add_annotation(x="2021-07-28", y=68000, text="5ª ola", showarrow=False, font=dict(family="Old Standard TT, serif", size=14, color="grey"), row=1, col=1)
fig.add_annotation(x="2022-01-10", y=68000, text="6ª ola", showarrow=False, font=dict(family="Old Standard TT, serif", size=14, color="grey"), row=1, col=1)

 # ajustes plot
fig.update_layout(hovermode = "x")
fig.update_yaxes(rangemode="tozero")
fig.update_layout(height=800, width=1000, title_text="Evolución COVID-19 en España")

fig.show()

In [4]:
 # creamos dataframe riesgo y no riesgo
df_gedad_0_39 = datos_covid[(datos_covid['grupo_edad']=='0-9')|(datos_covid['grupo_edad']=='10-19')|(datos_covid['grupo_edad']=='20-29')|(datos_covid['grupo_edad']=='30-39')].groupby(
    ['fecha'],as_index=False).agg({'num_casos': np.sum, 'num_def': np.sum})
df_gedad_40_49 = datos_covid[(datos_covid['grupo_edad']=='40-49')].groupby(
    ['fecha'],as_index=False).agg({'num_casos': np.sum, 'num_def': np.sum})
df_gedad_50_59 = datos_covid[(datos_covid['grupo_edad']=='50-59')].groupby(
    ['fecha'],as_index=False).agg({'num_casos': np.sum, 'num_def': np.sum})
df_gedad_60_69 = datos_covid[(datos_covid['grupo_edad']=='60-69')].groupby(
    ['fecha'],as_index=False).agg({'num_casos': np.sum, 'num_def': np.sum})
df_gedad_70_79 = datos_covid[(datos_covid['grupo_edad']=='70-79')].groupby(
    ['fecha'],as_index=False).agg({'num_casos': np.sum, 'num_def': np.sum})
df_gedad_80 = datos_covid[(datos_covid['grupo_edad']=='80+')].groupby(
    ['fecha'],as_index=False).agg({'num_casos': np.sum, 'num_def': np.sum})


 # creamos la visualizacion
fig = px.line(x = df_gedad_0_39['fecha'], y = df_gedad_0_39['num_def'], title = 'Número de defunciones por grupo de edad', 
              color = px.Constant('0-39 años'), labels = dict(x="fecha", y="número defunciones", color="Leyenda:"))
fig.add_trace(go.Scatter(x = df_gedad_40_49['fecha'], y = df_gedad_40_49['num_def'], name = "40-49 años", 
                         line_shape = 'spline', mode='lines', line = dict(color='green', width=1, dash='solid')))
fig.add_trace(go.Scatter(x = df_gedad_50_59['fecha'], y = df_gedad_50_59['num_def'], name = "50-59 años", 
                         line_shape = 'spline', mode='lines', line = dict(color='black', width=1, dash='solid')))
fig.add_trace(go.Scatter(x = df_gedad_60_69['fecha'], y = df_gedad_60_69['num_def'], name = "60-69 años", 
                         line_shape = 'spline', mode='lines', line = dict(color='grey', width=1, dash='solid')))
fig.add_trace(go.Scatter(x = df_gedad_70_79['fecha'], y = df_gedad_70_79['num_def'], name = "70-79 años", 
                         line_shape = 'spline', mode='lines', line = dict(color='orange', width=1, dash='solid')))
fig.add_trace(go.Scatter(x = df_gedad_80['fecha'], y = df_gedad_80['num_def'], name = "+80 años", 
                         line_shape = 'spline', mode='lines', line = dict(color='red', width=1, dash='solid')))

fig.update_layout(hovermode = "x")
fig.show()

In [5]:
 # agrupamos los datos por edad
df_gedad = datos_covid.groupby(['grupo_edad'],as_index=False).agg({'num_casos': np.sum, 'num_def': np.sum})

 # calculamos el porcentaje de mortalidad
def calc_porcentaje(x,y):
    return round(y/x*100,3)
df_gedad['perc_mort'] = df_gedad.apply(lambda x: calc_porcentaje(x.num_casos, x.num_def), axis=1)

 # eliminamos los registros con edad desconocida
df_gedad.drop([9], inplace=True) 

# creamos la visualización
z = df_gedad['perc_mort']
fig = go.Figure(data=[
    go.Bar(name = 'Numero de casos', x = df_gedad['grupo_edad'], y = df_gedad['num_casos'], customdata=z,
           text = df_gedad['num_casos'], textposition = 'outside'),
    go.Bar(name = 'Numero de defunciones', x = df_gedad['grupo_edad'], y = df_gedad['num_def'], customdata=z,
           text = df_gedad['num_def'], textposition = 'outside')])

 # ajustes plot
fig.update_layout(barmode='stack', title='Número de casos y defunciones por grupos de edad')
fig.update_traces(texttemplate='%{text:.0f}',
                 hovertemplate="<br>".join([
                "Edad: %{x}",
                "Cantidad: %{y}",
                "% mortalidad: %{customdata}"]))

fig.show()

In [6]:
fig = make_subplots(rows=4, cols=4, shared_xaxes=True, shared_yaxes=True, 
                    subplot_titles = ['Andalucia', 'Cataluña', 'Madrid', 'Valencia', 'Galicia',
                                      'Castilla y León','Canarias','País Vasco','Castilla-La Mancha', 'Región de Murcia',
                                      'Aragón', 'Islas Baleares', 'Extremadura', 'Asturias', 'Cantabria', 'La Rioja'])


df_ccaa = datos_covid.groupby(['codauto','fecha'], as_index=False).agg({'num_casos': np.sum, 'num_def': np.sum})


fig.add_trace(go.Scatter(x=df_ccaa[df_ccaa['codauto']==1]['fecha'], y=df_ccaa[df_ccaa['codauto']==1]['num_casos'], 
                         name = "Andalucia"), row=1, col=1)
fig.add_trace(go.Scatter(x=df_ccaa[df_ccaa['codauto']==2]['fecha'], y=df_ccaa[df_ccaa['codauto']==9]['num_casos'], 
                         name = 'Cataluña'), row=1, col=2)
fig.add_trace(go.Scatter(x=df_ccaa[df_ccaa['codauto']==3]['fecha'], y=df_ccaa[df_ccaa['codauto']==13]['num_casos'], 
                         name = 'Comunidad de Madrid'), row=1, col=3)
fig.add_trace(go.Scatter(x=df_ccaa[df_ccaa['codauto']==4]['fecha'], y=df_ccaa[df_ccaa['codauto']==10]['num_casos'], 
                         name = 'Comunidad Valenciana'), row=1, col=4)

fig.add_trace(go.Scatter(x=df_ccaa[df_ccaa['codauto']==9]['fecha'], y=df_ccaa[df_ccaa['codauto']==12]['num_casos'], 
                         name = 'Galicia'), row=2, col=1)
fig.add_trace(go.Scatter(x=df_ccaa[df_ccaa['codauto']==13]['fecha'], y=df_ccaa[df_ccaa['codauto']==7]['num_casos'], 
                         name = 'Castilla y León'), row=2, col=2)
fig.add_trace(go.Scatter(x=df_ccaa[df_ccaa['codauto']==1]['fecha'], y=df_ccaa[df_ccaa['codauto']==5]['num_casos'], 
                         name = 'Canarias'), row=2, col=3)
fig.add_trace(go.Scatter(x=df_ccaa[df_ccaa['codauto']==1]['fecha'], y=df_ccaa[df_ccaa['codauto']==16]['num_casos'], 
                         name = 'País Vasco'), row=2, col=4)

fig.add_trace(go.Scatter(x=df_ccaa[df_ccaa['codauto']==9]['fecha'], y=df_ccaa[df_ccaa['codauto']==8]['num_casos'], 
                         name = 'Castilla-La Mancha'), row=3, col=1)
fig.add_trace(go.Scatter(x=df_ccaa[df_ccaa['codauto']==13]['fecha'], y=df_ccaa[df_ccaa['codauto']==14]['num_casos'], 
                         name = 'Región de Murcia'), row=3, col=2)
fig.add_trace(go.Scatter(x=df_ccaa[df_ccaa['codauto']==1]['fecha'], y=df_ccaa[df_ccaa['codauto']==2]['num_casos'], 
                         name = 'Aragón'), row=3, col=3)
fig.add_trace(go.Scatter(x=df_ccaa[df_ccaa['codauto']==1]['fecha'], y=df_ccaa[df_ccaa['codauto']==4]['num_casos'], 
                         name = 'Islas Baleares'), row=3, col=4)

fig.add_trace(go.Scatter(x=df_ccaa[df_ccaa['codauto']==9]['fecha'], y=df_ccaa[df_ccaa['codauto']==11]['num_casos'], 
                         name = 'Extremadura'), row=4, col=1)
fig.add_trace(go.Scatter(x=df_ccaa[df_ccaa['codauto']==13]['fecha'], y=df_ccaa[df_ccaa['codauto']==3]['num_casos'], 
                         name = 'Asturias'), row=4, col=2)
fig.add_trace(go.Scatter(x=df_ccaa[df_ccaa['codauto']==1]['fecha'], y=df_ccaa[df_ccaa['codauto']==6]['num_casos'], 
                         name = 'Cantabria'), row=4, col=3)
fig.add_trace(go.Scatter(x=df_ccaa[df_ccaa['codauto']==1]['fecha'], y=df_ccaa[df_ccaa['codauto']==17]['num_casos'], 
                         name = 'La Rioja'), row=4, col=4)

 # ajustes plot
fig.update_layout(height=600, width=980, title_text="Evolución COVID-19 por CCAA")
fig.show()

In [7]:
 # agrupamos datos por sexo y semana
df_sexo = datos_covid.groupby(['sexo','semana'], as_index=False).agg({'num_casos': np.sum, 'num_def': np.sum, 'num_hosp': np.sum})
 # eliminamos registros con sexo desconocido
df_sexo = df_sexo[df_sexo['sexo']!='NC']
 
 # creamos dos plots
fig = make_subplots(rows=2, cols=1, shared_xaxes=False, subplot_titles =['Número de casos','Número de defunciones'])

 # 1 plot
fig.add_trace(go.Scatter(x=df_sexo[df_sexo['sexo']=='Hombres']['semana'], y=df_sexo[df_sexo['sexo']=='Hombres']['num_casos'],
                         name = "hombres casos", line_shape = 'spline', mode='lines', 
                         line = dict(color='green', width=2,dash='solid')), row=1, col=1)

fig.add_trace(go.Scatter(x=df_sexo[df_sexo['sexo']=='Mujeres']['semana'], y=df_sexo[df_sexo['sexo']=='Mujeres']['num_casos'], 
                         name = "mujeres casos", line_shape = 'spline', mode='lines', 
                         line = dict(color='goldenrod', width=2, dash='solid')), row=1, col=1)
 # 2 plot
fig.add_trace(go.Scatter(x=df_sexo[df_sexo['sexo']=='Hombres']['semana'], y=df_sexo[df_sexo['sexo']=='Hombres']['num_def'], 
                         name = "hombres defunciones", line_shape = 'spline', mode='lines', 
                         line = dict(color='green', width=2, dash='dashdot')), row=2, col=1)

fig.add_trace(go.Scatter(x=df_sexo[df_sexo['sexo']=='Mujeres']['semana'], y=df_sexo[df_sexo['sexo']=='Mujeres']['num_def'], 
                         name = "mujeres defunciones", line_shape = 'spline', mode='lines', 
                         line = dict(color='goldenrod', width=2, dash='dashdot')), row=2, col=1)

 # anotaciones plot
fig.add_annotation(x=13, y=40000, text="1ª ola", showarrow=True, arrowhead=4, row=1, col=1)
fig.add_annotation(x=40, y=60000, text="2ª ola", showarrow=True, arrowhead=4, row=1, col=1)
fig.add_annotation(x=52, y=125000, text="3ª ola", showarrow=True, arrowhead=4, row=1, col=1)
fig.add_annotation(x=67, y=40000, text="4ª ola", showarrow=True, arrowhead=4, row=1, col=1)
fig.add_annotation(x=80, y=100000, text="5ª ola", showarrow=True, arrowhead=4, row=1, col=1)
fig.add_annotation(x=101, y=150000, text="6ª ola", showarrow=True, arrowhead=4, row=1, col=1)

 # ajustes plot
fig.update_layout(hovermode = "x")
fig.update_layout(height=800, width=1000, title_text="Evolución COVID-19 por sexo y semana")
fig.show()

In [8]:
pop_cpro = pd.read_csv('datos/poblacion_edad_sexo.csv')
pop_cpro = pop_cpro.groupby(['cpro']).sum().reset_index()[['cpro','poblacion_total']]
pop_cpro['poblacion_total'] = 1000 * pop_cpro['poblacion_total']

num_casos_cpro = datos_covid.groupby(['cpro']).sum().reset_index()[['cpro','num_def']] #num_casos u otro

datos_mapa = pop_cpro.merge(num_casos_cpro,  how='inner')
navarra_missing = pd.DataFrame({"cpro": 31, "poblacion_total": np.NaN, "num_def": np.NaN}, index=[30])
datos_mapa = pd.concat([datos_mapa.iloc[:30], navarra_missing, datos_mapa.iloc[30:]]).reset_index(drop=True)

datos_mapa['perc'] = datos_mapa.apply(lambda x: x.num_def * 100 / x.poblacion_total, axis=1)

# MAPA
gdf = gpd.read_file("https://raw.githubusercontent.com/codeforgermany/click_that_hood/main/public/data/spain-provinces.geojson",
                    crs="epsg:4326")

gdf = gdf.sort_values(['cod_prov']).reset_index()
gdf["% defunciones"] = datos_mapa['perc']


px.choropleth_mapbox(gdf, geojson=gdf["geometry"].__geo_interface__, locations=gdf.index, color="% defunciones", 
                     hover_name="name", color_continuous_scale="matter", opacity=0.85
                    ).update_layout(
    mapbox={
        "style": "carto-positron", 
        "center": {
            "lon": sum(gdf.total_bounds[[0, 2]]) / 2,
            "lat": sum(gdf.total_bounds[[1, 3]]) / 2 + 0.5,
        },
        "zoom":4
    },
    margin={"l":0,"r":0,"t":30,"b":0},
    title='Porcentaje de defunción sobre la población provincial',
)

### En cada ola

In [9]:
df_1ola = datos_covid[(datos_covid['fecha']>'2020-03-10') & (datos_covid['fecha']<'2020-05-01')]
df_2ola = datos_covid[(datos_covid['fecha']>'2020-08-04') & (datos_covid['fecha']<'2020-12-01')]
df_3ola = datos_covid[(datos_covid['fecha']>'2020-12-09') & (datos_covid['fecha']<'2021-03-12')]
df_4ola = datos_covid[(datos_covid['fecha']>'2021-03-23') & (datos_covid['fecha']<'2021-05-22')]
df_5ola = datos_covid[(datos_covid['fecha']>'2021-07-05') & (datos_covid['fecha']<'2021-08-15')]
df_6ola = datos_covid[(datos_covid['fecha']>'2021-11-23') & (datos_covid['fecha']<'2022-01-03')]

mort1 = df_1ola['num_def'].sum()/df_1ola['num_casos'].sum()*100
mort2 = df_2ola['num_def'].sum()/df_2ola['num_casos'].sum()*100
mort3 = df_3ola['num_def'].sum()/df_3ola['num_casos'].sum()*100
mort4 = df_4ola['num_def'].sum()/df_4ola['num_casos'].sum()*100
mort5 = df_5ola['num_def'].sum()/df_5ola['num_casos'].sum()*100
mort6 = df_6ola['num_def'].sum()/df_6ola['num_casos'].sum()*100

lista_mort = [mort1, mort2, mort3, mort4, mort5, mort6]
lista_olas = ['1ª', '2ª', '3ª', '4ª', '5ª', '6ª']
lista_vac=[0,0,3,17.2,62.9,80.3]

# Create figure with secondary y-axis
fig = make_subplots(specs=[[{"secondary_y": True}]])

# Add traces
fig.add_trace(
    go.Scatter(x=lista_olas, y=lista_mort, name="% mortalidad", line_shape = 'spline'),
    secondary_y=False, 
)

fig.add_trace(
    go.Scatter(x=lista_olas, y=lista_vac, name="% vacunación", line_shape = 'spline'),
    secondary_y=True,
)

# Add figure title
fig.update_layout(title_text="Mortalidad y vacunación en las distintas olas")

# Set x-axis title
fig.update_xaxes(title_text="Olas")

# Set y-axes titles
fig.update_yaxes(title_text="% mortalidad", secondary_y=False)
fig.update_yaxes(title_text="% vacunación", secondary_y=True)

fig.update_layout(hovermode = "x")

fig.show()

perc_red_mort = (mort3-mort6)/mort3*100
print(f'El porcentaje de reducción de la mortalidad por COVID-19 entre la 3ª y la 6ª ola es: {perc_red_mort:.2f} %')
perc_red_hosp = (df_3ola['num_hosp'].sum()/df_3ola['num_casos'].sum()*100-(df_6ola['num_hosp'].sum()/df_6ola['num_casos'].sum()*100))/(df_3ola['num_hosp'].sum()/df_3ola['num_casos'].sum()*100)*100
print(f'El porcentaje de reducción de la hospitalización por COVID-19 entre la 3ª y la 6ª ola es: {perc_red_hosp:.2f} %')

El porcentaje de reducción de la mortalidad por COVID-19 entre la 3ª y la 6ª ola es: 93.38 %
El porcentaje de reducción de la hospitalización por COVID-19 entre la 3ª y la 6ª ola es: 81.98 %


### Durante los últimos tres meses

In [10]:
 # agrupamos los datos por edad de los ultimos 3 meses
df_gedad = datos_covid[datos_covid['fecha']>'2021-10-04'].groupby(['grupo_edad'],as_index=False).agg({'num_casos': np.sum, 'num_def': np.sum})

 # calculamos el porcentaje de mortalidad
def calc_porcentaje(x,y):
    return round(y/x*100,3)
df_gedad['perc_mort'] = df_gedad.apply(lambda x: calc_porcentaje(x.num_casos, x.num_def), axis=1)

 # eliminamos los registros con edad desconocida
df_gedad.drop([9], inplace=True) 

# creamos la visualización
z = df_gedad['perc_mort']
fig = go.Figure(data=[
    go.Bar(name = 'Numero de casos', x = df_gedad['grupo_edad'], y = df_gedad['num_casos'], customdata=z,
           text = df_gedad['num_casos'], textposition = 'outside'),
    go.Bar(name = 'Numero de defunciones', x = df_gedad['grupo_edad'], y = df_gedad['num_def'], customdata=z,
           text = df_gedad['num_def'], textposition = 'outside')])

 # ajustes plot
fig.update_layout(barmode='stack', title='Número de casos y defunciones por grupos de edad')
fig.update_traces(texttemplate='%{text:.0f}',
                 hovertemplate="<br>".join([
                "Edad: %{x}",
                "Cantidad: %{y}",
                "% mortalidad: %{customdata}"]))

fig.show()

In [11]:
 # creamos dataframe riesgo y no riesgo
df_riesgo = datos_covid[datos_covid['fecha']>'2021-10-04'][(datos_covid[datos_covid['fecha']>'2021-10-04']['grupo_edad']=='80+') | (datos_covid[datos_covid['fecha']>'2021-10-04']['grupo_edad']=='70-79')].groupby(
    ['fecha'],as_index=False).agg({'num_casos': np.sum, 'num_def': np.sum})

df_no_riesgo = datos_covid[datos_covid['fecha']>'2021-10-04'][(datos_covid[datos_covid['fecha']>'2021-10-04']['grupo_edad']!='80+') & (datos_covid[datos_covid['fecha']>'2021-10-04']['grupo_edad']!='70-79')].groupby(
    ['fecha'],as_index=False).agg({'num_casos': np.sum, 'num_def': np.sum})

 # creamos la visualizacion
fig = px.line(x = df_no_riesgo['fecha'], y = df_no_riesgo['num_def'], title = 'Número de defunciones mayores y menores de 70', 
              color = px.Constant('Menores de 70'), labels = dict(x="fecha", y="número defunciones", color="Leyenda:"))

fig.add_trace(go.Scatter(x = df_riesgo['fecha'], y = df_riesgo['num_def'], name = "Mayores de 70", 
                         line_shape = 'spline', mode='lines', line = dict(color='black', width=1, dash='solid')))

fig.update_layout(hovermode = "x")
fig.show()